In [34]:
from pyspark.sql import SparkSession
from pyspark.sql import SQLContext
from pyspark.sql.functions import date_format
from pyspark.sql.types import *
import pandas as pd
from pyspark.sql.functions import unix_timestamp, from_unixtime
#import plotly.graph_objs as go
#from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import shutil
#init_notebook_mode(connected=True)
spark = SparkSession.builder.appName("Python Spark SQL basic example").getOrCreate()
sc = spark.sparkContext
sqlContext = SQLContext(sc)
df = sqlContext.read.load('/test_dev/mba-code/dataset.csv', format='csv', header='true', inferSchema='true')
df.select("InvoiceNo", "StockCode", "Description", "Quantity", "InvoiceDate","InvoiceDateWS" ,date_format(from_unixtime(unix_timestamp('InvoiceDateWS', 'mm/dd/yyy')), 'EEEE').alias('weekday'),"CustomerID","Country").write.save("Invoices.parquet", format="parquet")
parquetFile = spark.read.parquet("Invoices.parquet")
# Parquet files can also be used to create a temporary view and then used in SQL statements.
parquetFile.createOrReplaceTempView("parquetFile")

In [57]:
#yield tuple(k.strip() for k in line.split(','))      
from operator import add
from apyori import apriori, load_transactions
import pyspark.sql.functions as f
def apriori_reader(association_rules):
    for rule in association_rules:
        yield rule
DescriptionGrp = spark.sql("SELECT distinct InvoiceNo,StockCode FROM parquetFile group by InvoiceNo,StockCode")
print(DescriptionGrp.rdd.take(2))
minSupport = 0.05 * DescriptionGrp.rdd.count()
apr_tem=DescriptionGrp.rdd.map(lambda x: (x[0], [x[1]])).reduceByKey(lambda x,y: x + y).collect()
pandas_mba_df = pd.DataFrame(apr_tem)
export_csv = pandas_mba_df.to_csv (r'/test_dev/mba-code/apriori_input.csv', index = None, header=False)
with open(r'/test_dev/mba-code/apriori_input.csv') as f:
    transactions = load_transactions(f, delimiter=",")
    results = list(apriori(transactions, min_support=0.5,min_confidence=0.7,min_lift=1.2,min_length=2))
    for x in range(len(results)): 
        print results[x]
#mba_list = pandas_mba_df.values.tolist()
#transactions = load_transactions(mba_list, delimiter=",")
#print(transactions)
#association_rules_mba=list(apriori(transactions,min_support=0.5,min_confidence=0.7,min_lift=1.2,min_length=2))
#next(association_rules_mba)



#association_rules=list(association_rules)
#rdd = DescriptionGrp.rdd.filter(lambda x: x[0][2] == x[1][2])
#items_tuple = DescriptionGrp.rdd.map(lambda x: (x[0], list(set(x[1]))))
#items_tuple.collect()
#items = DescriptionGrp.rdd.flatMap(lambda line:line.split(","))
#DescriptionGrp.rdd.take(100).groupByKey().collect()
#items_tuple = items.map(lambda x: (x[0], list(set(x[1]))))
#items.collect()
#df_new = DescriptionGrp.toPandas().apply(pd.Series).unstack().reset_index()
#spDF = sqlContext.createDataFrame(df_new)
#print(items_tuple.take(5))
#itemCount = spDF.rdd.map(lambda item:(item, 1)).reduceByKey(add)
#print(itemCount.take(5))
#l1 = itemCount.filter(lambda (i,c): c > minSupport)
#print(l1.take(5))
#l1.take(5)

[Row(InvoiceNo=u'549099', StockCode=u'21908'), Row(InvoiceNo=u'549101', StockCode=u'22586')]
['564551', "[u'22667', u'22865', u'22666', u'22114', u'23212', u'22904', u'22348', u'20914']"]
['560692', "[u'22665', u'21733', u'21078', u'48194', u'21041', u'22904', u'21080', u'21654', u'22469', u'23321', u'21899', u'23178', u'22666', u'22193', u'22427', u'22507', u'20914', u'22095', u'23302', u'84596G', u'22667', u'21164', u'20832', u'21294', u'84974', u'85123A', u'84596B', u'23198', u'23106', u'21218', u'22097', u'20676', u'22094', u'21034']"]
['561079', "[u'21819', u'23313', u'85049E', u'22602', u'23091', u'22910', u'23321', u'22558', u'22086', u'20754', u'21217', u'22816', u'22487', u'22801', u'84879', u'22460', u'23234', u'22336', u'22694', u'22081', u'23103', u'35953', u'82484', u'22191', u'20983', u'20749', u'47590B', u'85014B', u'22571', u'22427', u'22580', u'20718', u'35954', u'21264', u'22079', u'22818', u'20751', u'84754', u'21563', u'22600', u'20756', u'20750', u'20725', u'23130'

['574287', "[u'21809', u'22578', u'90161B', u'22222', u'21817', u'22696', u'21811', u'23490', u'21922', u'22579', u'21123', u'90161C', u'21818', u'21126', u'21381', u'22556', u'35954', u'85034A', u'21810', u'90200A', u'21819', u'23045', u'23101', u'22082', u'22457', u'22937', u'21034', u'90200E', u'23499', u'22091', u'23301', u'85035C', u'21380', u'22577', u'21592', u'22340', u'22164', u'22095', u'21121', u'21122', u'22785', u'84879', u'21621', u'90200B', u'22163', u'20668', u'22338', u'23466', u'22155', u'22599', u'71270', u'21591', u'22597']"]
['565245', "[u'22554', u'22558', u'22621', u'22037', u'22555', u'22718', u'22652', u'22996', u'22915', u'22961']"]
['571028', "[u'22110', u'22130', u'22111', u'22910', u'22579', u'85211', u'21803', u'23265', u'84029G', u'23103', u'22694', u'22998', u'21807', u'21818', u'23266', u'23263', u'20686', u'23329', u'23264', u'85061W', u'21802', u'22572', u'47591D', u'22577', u'48194', u'21159', u'21733', u'22571', u'22578', u'23275', u'23211', u'23210

['549323', "[u'22150', u'23230', u'22523', u'22147', u'22515', u'22514', u'22027', u'22693', u'22431', u'22520', u'22526', u'22432', u'22516', u'22025', u'22492', u'22522', u'22711', u'21790', u'22517', u'22521', u'20973', u'22518', u'22519']"]
['561570', "[u'48116', u'48194', u'48173C', u'23144']"]
['C569891', "[u'23165', u'22294', u'22720', u'23407', u'84609', u'23263', u'22588', u'21722']"]
['549459', "[u'62043B']"]
['571706', "[u'21931', u'85035C', u'85034B', u'23505', u'85034A', u'20712', u'85035B', u'85034C']"]
['570796', "[u'22086', u'72816', u'23321', u'22413', u'23368', u'22385', u'23182', u'23507', u'22952', u'22095', u'22355', u'21823', u'22186', u'22578', u'22099', u'22577', u'23202', u'72818', u'21733', u'23503', u'85123A', u'23506', u'21929', u'22411', u'22661', u'72817', u'23103', u'85150', u'22412', u'23367', u'23322', u'21169', u'23201', u'22910', u'22909', u'23319', u'85099B', u'22579', u'22386', u'22950', u'21903']"]
['C562160', "[u'22456']"]
['563437', "[u'23232', u

['539034', "[u'21258', u'22910', u'22086', u'22748', u'20727', u'22634', u'20725', u'85123A', u'21156', u'22746', u'84032B', u'47591D', u'21257', u'21259', u'22745', u'21484', u'22968', u'22444', u'22384', u'22112', u'22326']"]
['565084', "[u'22616', u'22988', u'22659', u'22970', u'22902', u'23309']"]
['562526', "[u'21523', u'22690', u'22561', u'21623', u'48187', u'22499', u'22197', u'21028', u'21621', u'20685', u'21025', u'21955', u'22616', u'21175', u'22084', u'21026', u'48138', u'21027']"]
['562445', "[u'21843', u'POST', u'23014', u'22624', u'22398', u'20682', u'23546', u'21481', u'22852', u'85014A', u'23245', u'23286', u'23287', u'23013', u'23267', u'22702', u'22840', u'23315', u'22915', u'21770', u'23548']"]
['578341', "[u'22561', u'21703']"]
['543541', "[u'22784', u'21232', u'21472', u'22105', u'48111', u'20961', u'84945', u'21217', u'21730', u'22103', u'21313', u'22061', u'85123A', u'22508', u'22890', u'47559B', u'37450', u'48138', u'84212', u'22423', u'21317', u'21324', u'22178

['563358', "[u'82494L', u'23096', u'82486', u'21754', u'21755', u'23118', u'21363', u'22794', u'21332', u'82482', u'84792', u'72598', u'72122', u'22119', u'23111']"]
['561507', "[u'22544', u'22539', u'21559', u'22382', u'22423', u'20838', u'22099', u'21452', u'22326', u'22540', u'22131', u'22029', u'22399', u'22138', u'23010', u'22554', u'23240', u'20840', u'23236', u'20725', u'22534', u'22530', u'22489', u'POST', u'22483', u'22727', u'22726', u'22551', u'20726', u'22636', u'22662', u'22630', u'22838', u'22180', u'22505', u'22716', u'23290', u'23245', u'22961', u'22617', u'21055', u'22328', u'22646', u'23346', u'23243', u'23289', u'23293', u'22320', u'22644', u'84509A', u'23291', u'23292', u'21430', u'22614', u'23241', u'23206', u'22631', u'22720', u'20837', u'22492', u'23345', u'22652', u'21918', u'22899', u'23007', u'22556', u'22969', u'23008', u'22139', u'23209']"]
['545826', "[u'82486', u'21498', u'22807', u'22090', u'22088', u'17084R', u'16237', u'16161U', u'85039A', u'21499', u'2

...

['543179', "[u'22536', u'22268', u'22534', u'22539', u'22546', u'22359', u'22620', u'22531', u'10002', u'22364', u'22492', u'22495', u'22494', u'22558', u'22489', u'22496', u'22267', u'84077', u'22406', u'22407', u'22540', u'22532', u'22541', u'22410', u'22258', u'21745', u'22567', u'22257', u'22409', u'22544', u'22533', u'22256', u'22408', u'22543', u'22360', u'22405', u'22561']"]
['577473', "[u'22278', u'22630', u'22093', u'21064', u'21592', u'21993', u'21832', u'21169', u'22620', u'20763', u'21506', u'85178', u'22750', u'23203', u'23154', u'23570', u'22100', u'22972', u'23423', u'82582', u'20982', u'23346', u'22659', u'22363', u'23194', u'22720', u'22553', u'23177', u'22907', u'21557', u'23198', u'20781', u'21500', u'23089', u'22551', u'22948', u'20983', u'23494', u'23176', u'22098', u'21497', u'21584', u'22114', u'22096', u'22532', u'22182', u'22992', u'22131', u'47567B', u'22197', u'22382', u'22962', u'23114', u'22364', u'20728', u'23582', u'23299', u'22097', u'85177', u'22360', u

['C566467', "[u'23321', u'20723', u'22355', u'23205', u'23298', u'23201', u'22380', u'20719', u'85099F', u'23199', u'20724', u'85099B', u'23204', u'21212', u'20725', u'20728', u'21931', u'22197', u'84991', u'22356', u'22998', u'22384']"]
['555157', "[u'23169', u'47566', u'47590B', u'23075', u'47590A', u'22849', u'22423', u'82580']"]
['575191', "[u'23245', u'85049A', u'21260', u'85099B', u'22946']"]
['C562957', "[u'22842', u'22540']"]
['546430', "[u'22243', u'22285', u'22318', u'20711', u'22176', u'20724', u'22245', u'22244', u'22320', u'47566', u'22467', u'84849D', u'21622', u'22077', u'22319', u'22325', u'22212', u'22175', u'21135', u'22284', u'22317']"]
['577557', "[u'84347', u'22725', u'23500', u'23000', u'21985', u'21212', u'23300', u'23307', u'23271', u'22579', u'21990', u'22996', u'23035', u'82482', u'17091J', u'21636', u'47503A', u'23399', u'21137', u'23489', u'21158', u'21976', u'22639', u'82483', u'23402', u'84991', u'84926E', u'15039', u'21162', u'21993', u'85130B', u'22577',

['572232', "[u'22632', u'22086', u'23083', u'23320', u'22866', u'23439', u'22867', u'22950', u'23344', u'23100', u'23319', u'23378']"]
['568165', "[u'85123A', u'23136', u'20975', u'22276', u'22499', u'82486', u'82483', u'22776', u'22789', u'21745', u'22508', u'23366', u'22277', u'84832', u'20724', u'85099B', u'72760B', u'20718', u'21621', u'82482', u'22094', u'22457', u'82494L', u'84970L', u'84836', u'82484', u'22296', u'21624', u'85066', u'20754', u'23298', u'23152', u'23240', u'22669', u'22189', u'21411', u'20752']"]
['562839', "[u'21155', u'22120', u'22616', u'22556', u'22691', u'23309', u'23244', u'22896', u'22553', u'22974', u'22900', u'20981', u'23188', u'22726', u'22730', u'23280', u'23169', u'22554']"]
['C560822', "[u'M']"]
['551020', "[u'22719']"]
['568158', "[u'23294', u'23519', u'22847', u'84832', u'22139', u'21791', u'21484', u'23516', u'85178', u'84029E', u'23502', u'22812', u'20749', u'46000S', u'23514', u'23511', u'PADS', u'23517', u'23240', u'21683', u'35970', u'22813',

['541703', "[u'21365', u'22380', u'20726', u'22549', u'22466', u'POST', u'22379', u'22381', u'20728', u'22139', u'21371', u'71270']"]
['563711', "[u'23032', u'22775', u'21671', u'21672', u'22771', u'21668', u'22774']"]
['562781', "[u'20981', u'22795', u'21900', u'22457', u'23300', u'48187', u'84378', u'21983', u'21899', u'21524', u'21677', u'20982', u'48194', u'22227', u'84945', u'47591D', u'21985', u'22077', u'22692', u'21523', u'23301', u'21982', u'48116']"]
['548095', "[u'20850']"]
['563658', "[u'20682', u'20832', u'21216', u'84660A', u'20749', u'15060B', u'23243']"]
['572025', "[u'23209', u'22779', u'23343', u'20728', u'23198', u'22175', u'21108', u'23366', u'23200', u'23243', u'23344', u'20992', u'22379', u'23367', u'23275', u'22896', u'22424', u'90058B', u'22549', u'22381', u'22897', u'35599D']"]
['575037', "[u'23371', u'22142', u'20750', u'22144', u'22579', u'23301', u'22578', u'23557', u'22075', u'23372', u'23554', u'23284', u'20972', u'22577', u'22086', u'20767', u'23556', u'2

['574324', "[u'23355']"]
['537394', "[u'22960', u'22963', u'22558', u'22961', u'22962']"]
['C557004', "[u'85159B']"]
['576094', "[u'22554', u'22557', u'22556', u'23296', u'23293', u'22197', u'23294', u'21592', u'22555', u'23583']"]
['561010', "[u'21401', u'20725', u'21400', u'23295', u'22433', u'23293', u'35924', u'20971', u'47559B', u'23309', u'22432', u'22961', u'21213']"]
['575154', "[u'22661', u'20719', u'POST', u'22423', u'22029', u'21731', u'22727', u'21914', u'22728', u'22507', u'23108', u'23084', u'22726']"]
['569133', "[u'47504K', u'35954', u'47503A', u'35471D', u'22403', u'22609', u'35598D', u'84927F', u'22402', u'20974', u'47504H', u'22400', u'22338', u'84926F', u'72818', u'35933', u'84078A', u'22339', u'21916', u'20973', u'72817']"]
['576083', "[u'23295', u'23231', u'22708', u'23296', u'23236', u'23494', u'22139', u'22045', u'23545', u'84077', u'23293']"]
['C576232', "[u'22138', u'21259']"]
['552878', "[u'22962', u'22530', u'23232', u'22716', u'22813', u'21122', u'POST', u'